# **L3 Algèbre effective — TP 1  du mardi 17 septembre 2019**
 
## **Pgcd, algorithme d'Euclide et relations de Bezout**

## I La suite de Fibonacci

On rappelle que la suite de Fibonacci est la suite linéaire récurrente définie par 
$$ u_0=1 \qquad u_1=1 \qquad \text{ et } \qquad \forall n \geq 2,\ u_{n}=u_{n-1}+u_{n-2}.$$
Pour évaluer le 100ème terme de la suite, il est tentant d'implémenter la suite de manière récursive. 

Faîtes le. Que remarquez-vous? Pourquoi?

In [38]:
def fib(n):
    if n==0:
        return 1
    elif n==1:
        return 1
    else:
        return fib(n-1)+fib(n-2)

In [39]:
fib(10)

89

Le calcul de ```fib(100)``` est trop long: en effet, l'implémentation récursive est ici particulièrement inappropriée puisque l'on refait beaucoup de fois les mêmes calculs. Le nombre d'appels de la fonction ```fib``` pour calculer ```fib(n)``` est de l'ordre de $2^{n-2}$. Pour $n=100$, c'est trop grand!

In [40]:
2^100

1267650600228229401496703205376

**On implémente donc de manière iétrative: on calcule tous les termes de la suite de $u_0$ jusqu'à $u_n$ en ne gardant en mémoire que les deux derniers termes.**

In [41]:
def fib_it(n):
    if n==0:
        return 1
    elif n==1:
        return 1
    else:
        i=1
        a=1
        d=1
        while (i<n):
            i=i+1
            aux=a
            a=d
            d=d+aux
        return d

In [42]:
fib_it(100), fib_it(10000)

(573147844013817084101,
 544383731135652813387342609937503801353891845546959670262477158412085828656223490170830515479389605411738226759780263173843595847511162414391747026429591699255863341179060630480897935314761084662590727593678991506779600883065979666419658249377218003814411588410424809979846964873753371800281637633177819279411013692627509795098007135967180238147106699126442147752544785876745689638080029622651331113599297627266794414001015758000435107774659358053625024617079180592264146790056907523218958681423678495938807564234837543863426396359707337562600989624626687461120417398194048750624437098686543156268471861956201461266422327118150403670188252053148458758171935335298278378003519025292395178366894676619179538847124410284639354494846144507787625295209618875972728892207685373964758695431591724345371936112637439263373130058961672480517379863063681150030883967495871026195246313524474995052041983051871683216232838597946272459197714546282183996957892237989121994317754697052161310

**On peut alors aller loin dans le calcul des termes...**

## **II -Pgcd**

a) Trouver dans l'aide la fonction Sage qui permet de calculer le pgcd de deux entiers.

Faire quelques tests: 
pgcd(5,6)=?
pgcd(0,6)=?
pgcd(0,0)=?


**En Sage, la fonction ```gcd``` permet de calculer le pgcd de deux entiers.
On obtient l'aide associée en tapant ``` help(gcd)``` ou bien ``` gcd?```.**

In [43]:
gcd(5,6)

1

In [2]:
gcd?

1

Un premier objectif de ce TP est de reprogrammer cette fonction vous même, en utilisant l'algorithme d'Euclide.

b) Quelle fonction permet en Sage de calculer le reste dans une division euclidienne? Et le quotient?

Quelle est la division euclidienne de 1234 par 7?

**On calcule le reste avec ```%``` et le quotient avec ```//```.**

In [44]:
1234%7

2

In [45]:
1234//7

176

In [46]:
1234==(1234//7)*7+(1234%7)

True

Pour $0\leq m \leq n$, quelle est la division euclidienne de $m$ par $n$?

Quelle relation y a-t-il entre la division euclidienne de $m$ par $n$ et celle de $m+n$ par $n$?


En utilisant les remarques ci-dessus, écrivez un programme **récursif** qui calcule la division euclidienne du premier argument par le second (s'il est non nul).


**Pour $0\leq m \leq n$, la division euclidienne de $m$ par $n$ est $$m=0\cdot n + m.$$
Si $m=qn+r$ est la division euclidienne de $m$ par $n$, alors $m+n=(q+1)\cdot n+r$ est la division euclidienne de $m+n$ par $n$. On en déduit le programme récursif ci-dessous.**


In [47]:
def div(m,n):
    if (n==0):
        return "Division par zero"
    elif (m<n):
        return([0,m])
    else:
        aux=div(m-n,n)
        return(aux[0]+1,aux[1])
    

In [48]:
div(512,3)

(170, 2)

c) Compléter la fonction ci-dessous pour qu'elle calcule le pgcd des arguments.
Plusieurs approches sont possibles, dont:
1) Une boucle 
2) Une fonction récursive

**On présente les deux variantes.**

In [49]:
def pgcd(m,n):
    a,b=m,n
    while(b<>0):
        aux=b
        b=a%b
        a=aux
    return a


In [50]:
def pgcdRec(m,n):
    if (n==0):
        return m
    else:
        return pgcdRec(n,m%n)

In [53]:
pgcd(0,5)

5

**d-1.)** Pour évaluer la "complexité" du calcul du pgcd, on pourrait commencer par compter le nombre de divisions euclidiennes effectuées. Faîtes le.


**On rajoute un compteur dans le programme précédent.**

In [55]:
def pgcd(m,n):
    compteur=0
    a,b=m,n
    while(b<>0):
        compteur=compteur+1
        aux=b
        b=a%b
        a=aux
    return(a, compteur)

In [56]:
pgcd(fib(10),fib(9))

(1, 9)

In [57]:
pgcd(fib(10)-1,fib(9))

(11, 4)

In [58]:
pgcd(fib(10)-2,fib(9))

(1, 7)

**On remarque que le nombre d'itérations semble assez chaotique: pour des entiers très proches, cela varie, et pas du tout linéairement.**

**d-2)** Une façon d'améliorer la complexité ci-dessus est de ne pas utiliser des divisions euclidiennes *stricto sensu*, mais des divisions avec restes possiblement négatifs.
Remarquer que si *a*>*b*>0 sont des entiers, alors il existe une division avec reste:

*a=bq+r*, **avec |r|≤ b/2**

(Noter  qu'ici, *r* est potentiellement négatif!) et qu'alors, on a *pgcd(a,b)=pgcd(b,|r|)*.

Utiliser cette remarque pour proposer un calcul du pgcd plus rapide que le précédent et comparer le nombre d'opérations.


**On commence par coder le nouveau reste de la division euclidienne sophistiquée.**

In [67]:
def reste(m,n):
    if (n==0):
        return "Division par zero"
    elif abs(m)<= abs(n)//2:
        return m
    else:
        return reste(abs(m)-abs(n),n)

In [68]:
reste(5,-1)

0

**On peut alors reprendre le même programme qu'avant, en utilisant juste la nouvelle fonction reste.**

In [88]:
def pgcd2(m,n):
    compteur=0
    a,b=m,n
    while(b<>0):
        compteur=compteur+1
        aux=b
        b=reste(a,b)
        a=aux
    return(a, compteur)

In [76]:
pgcd2(fib(10),fib(9)),pgcd2(fib(10)-1,fib(9)),pgcd2(fib(10)-2,fib(9))

((-1, 5), (11, 3), (1, 5))

**La fonction pgcd2 a bien l'air meilleure. Pour tester plus, on tire au hasard quelques entiers et on compare les deux fonctions.**

In [93]:
for i in range(100):
    a=randint(1,10000)
    b=randint(1,10000)
    p1=pgcd(a,b)
    p2=pgcd2(a,b)
    print(p1[1]/(p2[1]+0.))

1.00000000000000
1.25000000000000
1.12500000000000
1.42857142857143
1.60000000000000
1.40000000000000
1.83333333333333
1.50000000000000
1.00000000000000
1.42857142857143
1.42857142857143
1.60000000000000
1.50000000000000
1.40000000000000
1.00000000000000
1.33333333333333
1.37500000000000
1.00000000000000
1.25000000000000
1.50000000000000
1.14285714285714
1.50000000000000
1.14285714285714
1.44444444444444
1.33333333333333
1.66666666666667
1.16666666666667
1.75000000000000
1.22222222222222
1.33333333333333
1.00000000000000
1.60000000000000
1.00000000000000
1.60000000000000
1.33333333333333
1.20000000000000
1.00000000000000
1.80000000000000
1.50000000000000
1.14285714285714
1.40000000000000
1.20000000000000
1.25000000000000
1.25000000000000
1.25000000000000
1.20000000000000
1.20000000000000
1.25000000000000
1.50000000000000
1.28571428571429
1.16666666666667
1.66666666666667
1.00000000000000
1.28571428571429
1.50000000000000
1.20000000000000
1.33333333333333
1.42857142857143
1.142857142857

**La fonction pgcd2 semble bien meilleure.**

e) Implémenter une fonction *pgcdbin* utilisant l'algorithme binaire (faire une recherche si nécessaire).

In [2]:
def pgcdbin(m,n):
    if (m==n):
        return m
    elif (m%2==0) and (n%2==0):
        return 2*pgcdbin(m/2,n/2)
    elif (m%2==0): # n est alors impair
        return pgcdbin(m/2,n)
    elif (n%2==0):
         return pgcdbin(m,n/2)
    elif (m>n):
        return pgcdbin((m-n)/2,n)
    else:
        return pgcdbin((n-m)/2,m)

In [3]:
pgcdbin(45,15)

15

f) Quelle fonction en sage permet de trouver les coefficients d'une relation de Bézout?

Donner une relation de Bézout entre 779 et 123.

**Les coefficients de Bezout se calculent en utilisant la fonction ```xgcd```.**

In [0]:
xgcd?

In [12]:
B=xgcd(779,123)

In [14]:
B[0]==779*B[1]+123*B[2]

True

Compléter la fonction suivante pour qu'elle calcule une relation de Bézout entre les arguments.

Plusieurs approches sont possibles, dont
1) Calquer la méthode "humaine" qui consiste à remonter l'algorithme d'Euclide. Pour cela, il faut créer des listes en sage pour stocker les valeurs des quotients successifs dans l'algorithme d'Euclide
2) Si r est le reste de la division euclidienne de m par n, trouver un lien entre Bezout(m,n) et Bezout(n,r).
En déduire une variante récursive.

**Pour la première méthode, il faut créer la liste des quotients dans l'algorithme d'Euclide. Les listes sont codées par des suites entre crochets, par exemple ```[1,2,3]```. La fonction ```+``` permet de concaténer deux listes. On fait alors la remontée en changeant les coefficients au fur et à mesure.**

In [4]:
def Bezout(m,n):
    L=[]
    while(n<>0):
        aux=n
        n=m%n
        L=L+[m//aux]
        m=aux
    i=len(L)-2
    u=1
    v=-L[i]
    while(i>0):
        i=i-1
        aux=v
        v=u-L[i]*v
        u=aux
    return([u,v])

In [5]:
Bezout(779,123)

[1, -6]

**Pour la méthode récursive, on remarque que si l'on injecte $m=nq+r \iff r=m-nq$ dans une relation de Bézout pour $n$ et $r$, disons $un+vr=d$, on obtient une relation de Bezout pour $m$ et $n$ de la forme
$d=un+v(m-nq)=vm+(u-nv)n$. D'où le programme récursif suivant:**

In [6]:
def BezRec(m,n):
    if (n==0):
         return [1,0]
    else:
        aux=BezRec(n,m%n)
        return [aux[1],aux[0]-m//n*aux[1]]

Testez votre fonction.

In [8]:
BezRec(779,123)

[1, -6]

## III - Ecriture triadique (=en base 3)

Ecrire une fonction *triad* qui renvoie (sous forme de liste) l'écriture d'un entier en base *3*.

In [10]:
def triad(n):
    if (n<3):
        return [n]
    else:
        u=n%3
        return triad((n-u)/3)+[u]

In [12]:
triad(23)

[2, 1, 2]